## Logistic Regression

#### Importing libraries

In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
import matplotlib.pyplot as plt
import numpy as np
from sklearn.metrics import classification_report, recall_score, precision_score, accuracy_score, f1_score
from itertools import combinations
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
import warnings
warnings.filterwarnings('ignore')

#### Importing Attrition CSV File and dropping null values

In [34]:
df = pd.read_csv("../WA_Fn-UseC_-HR-Employee-Attrition.csv")
df = df.dropna(axis='columns', how='all')
df.head()

Age Attrition     BusinessTravel  DailyRate              Department  \
0   41       Yes      Travel_Rarely       1102                   Sales   
1   49        No  Travel_Frequently        279  Research & Development   
2   37       Yes      Travel_Rarely       1373  Research & Development   
3   33        No  Travel_Frequently       1392  Research & Development   
4   27        No      Travel_Rarely        591  Research & Development   

   DistanceFromHome  Education EducationField  EmployeeCount  EmployeeNumber  \
0                 1          2  Life Sciences              1               1   
1                 8          1  Life Sciences              1               2   
2                 2          2          Other              1               4   
3                 3          4  Life Sciences              1               5   
4                 2          1        Medical              1               7   

   ...  RelationshipSatisfaction StandardHours  StockOptionLevel  \
0  ...                         1            80                 0   
1  ...                         4            80                 1   
2  ...                         2            80                 0   
3  ...                         3            80                 0   
4  ...                         4            80                 1   

   TotalWorkingYears  TrainingTimesLastYear WorkLifeBalance  YearsAtCompany  \
0                  8                      0               1               6   
1                 10                      3               3              10   
2                  7                      3               3               0   
3                  8                      3               3               8   
4                  6                      3               3               2   

  YearsInCurrentRole  YearsSinceLastPromotion  YearsWithCurrManager  
0                  4                        0                     5  
1                  7                        1                     7  
2                  0                        0                     0  
3                  7                        3                     0  
4                  2                        2                     2  

[5 rows x 35 columns]

#### Adding new variables

In [38]:
# Adding new variables
# Drop the null rows
monthlyIncomeBins = [0,2000,4000,6000,8000,10000,20000]
monthlyIncomeLabels = [0,1,2,3,4,5]
df['MonthlyIncomeBins'] = pd.cut(df['MonthlyIncome'], bins=monthlyIncomeBins, labels=monthlyIncomeLabels)
df['Time_in_each_comp'] = (df['Age']-20) / ((df)['NumCompaniesWorked']+1)
df['TotalSatisfaction_mean'] = (df['RelationshipSatisfaction']  + df['EnvironmentSatisfaction'] + df['JobSatisfaction'] + df['JobInvolvement'] + df['WorkLifeBalance'])/5
df['Income_YearsComp'] = df['MonthlyIncome'] / df['YearsAtCompany']
df['Income_YearsComp'] = df['Income_YearsComp'].replace(np.Inf, 0)
df['Income_Distance'] = df['MonthlyIncome'] / df['DistanceFromHome']
df['Fidelity'] = (df['NumCompaniesWorked']) / df['TotalWorkingYears']
df['Fidelity'] = df['Fidelity'].replace(np.Inf, 0)
df['Stability'] = df['YearsInCurrentRole'] / df['YearsAtCompany']
df['Stability'].fillna((df['Stability'].mean()), inplace=True)
df['Hrate_Mrate'] = df['HourlyRate'] / df['MonthlyRate']
def SalesDpt(df) :
    if df['Department'] == 'Sales':
        return 1
    else:
        return 0
df['SalesDpt'] = df.apply(lambda df:SalesDpt(df) ,axis = 1)
df.columns

Index(['Age', 'Attrition', 'BusinessTravel', 'DailyRate', 'Department',
       'DistanceFromHome', 'Education', 'EducationField', 'EmployeeCount',
       'EmployeeNumber', 'EnvironmentSatisfaction', 'Gender', 'HourlyRate',
       'JobInvolvement', 'JobLevel', 'JobRole', 'JobSatisfaction',
       'MaritalStatus', 'MonthlyIncome', 'MonthlyRate', 'NumCompaniesWorked',
       'Over18', 'OverTime', 'PercentSalaryHike', 'PerformanceRating',
       'RelationshipSatisfaction', 'StandardHours', 'StockOptionLevel',
       'TotalWorkingYears', 'TrainingTimesLastYear', 'WorkLifeBalance',
       'YearsAtCompany', 'YearsInCurrentRole', 'YearsSinceLastPromotion',
       'YearsWithCurrManager', 'MonthlyIncomeBins', 'Time_in_each_comp',
       'TotalSatisfaction_mean', 'Income_YearsComp', 'Income_Distance',
       'Fidelity', 'Stability', 'Hrate_Mrate', 'SalesDpt'],
      dtype='object')

#### Selecting Features

In [43]:
features = ['OverTime', 'Time_in_each_comp', 'Fidelity', 'Stability', 'YearsWithCurrManager', 
           'StockOptionLevel', 'Hrate_Mrate', 'HourlyRate', 'SalesDpt',           
           'PerformanceRating','MaritalStatus','Gender', 'Education', 'TrainingTimesLastYear',
           'TotalSatisfaction_mean', 'Income_YearsComp', 'Income_Distance']

print("Total Features : "+str(len(features)))
features

Total Features : 17


['OverTime',
 'Time_in_each_comp',
 'Fidelity',
 'Stability',
 'YearsWithCurrManager',
 'StockOptionLevel',
 'Hrate_Mrate',
 'HourlyRate',
 'SalesDpt',
 'PerformanceRating',
 'MaritalStatus',
 'Gender',
 'Education',
 'TrainingTimesLastYear',
 'TotalSatisfaction_mean',
 'Income_YearsComp',
 'Income_Distance']

#### Creating X and y for Model (total features)

In [60]:
data=df[features]
data_binary_encoded = pd.get_dummies(data)
X=data_binary_encoded
y=df["Attrition"].replace({'Yes': 1, 'No': 0})
X.shape

(1470, 21)

#### Creating a Function that runs Logistic Regression Model and returns a list with:
[Train Score, Test Score, Precision Score, Accuracy Score, F1 Score, Recall Score, Classification Report]

In [78]:
def createModel(X):
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1)
    X_scaler = MinMaxScaler().fit(X_train)
    X_train_scaled = X_scaler.transform(X_train)
    X_test_scaled = X_scaler.transform(X_test)
    model = LogisticRegression()
    model = model.fit(X_train_scaled, y_train)
    trainScore = model.score(X_train_scaled,y_train)
    testScore = model.score(X_test_scaled,y_test)
    test = model.predict(X)
    precisionScore = precision_score(y,test)
    accuracyScore = accuracy_score(y,test)
    f1Score = f1_score(y,test)
    recallScore = recall_score(y,test)
    classRep = classification_report(y,test)
    retList = [trainScore, testScore, precisionScore, accuracyScore, f1Score, recallScore, classRep]
    return retList

modelResults = createModel(X)
print("Classification Report:")
print(modelResults[6])

Classification Report:
              precision    recall  f1-score   support

           0       0.84      1.00      0.91      1233
           1       0.00      0.00      0.00       237

    accuracy                           0.84      1470
   macro avg       0.42      0.50      0.46      1470
weighted avg       0.70      0.84      0.77      1470



Even though our initial model has 88% and 85% Test and Train Scores, Precision and F1 Scores were 0. The model is overtrained, to get the best results and lower the amount of variables needed BRUTE FORCE was applied. Following code runs a model for every combination of variables. 

In [79]:
testCombinations = []
for i in range(6, len(features)):
    testCombinations += list(combinations(features, i))

print(f'Total Combinations: {len(testCombinations)}')

Total Combinations: 121669


In [7]:
minCombinations = 6
newFeatures = []
for i in range(minCombinations, len(features)):
    newFeatures += list(combinations(features, i))

# Uncomment the next line to create a fast example
#newFeatures = list(combinations(features, len(features)-1))
scores = []
counter = 1

for i in newFeatures:
    print(f'Progress {round(counter/len(newFeatures)*100,1)}% {counter}/{len(newFeatures)}')
    counter += 1
    newDF = df.filter(i, axis=1)
    X = pd.get_dummies(newDF)
    retList = createModel(X)
    retList.append(i)
    scores.append(retList)

print("Models processing complete!")

Progress 0.0% 1/121669
Progress 0.0% 2/121669
Progress 0.0% 3/121669
Progress 0.0% 4/121669
Progress 0.0% 5/121669
Progress 0.0% 6/121669
Progress 0.0% 7/121669
Progress 0.0% 8/121669
Progress 0.0% 9/121669
Progress 0.0% 10/121669
Progress 0.0% 11/121669
Progress 0.0% 12/121669
Progress 0.0% 13/121669
Progress 0.0% 14/121669
Progress 0.0% 15/121669
Progress 0.0% 16/121669
Progress 0.0% 17/121669
Progress 0.0% 18/121669
Progress 0.0% 19/121669
Progress 0.0% 20/121669
Progress 0.0% 21/121669
Progress 0.0% 22/121669
Progress 0.0% 23/121669
Progress 0.0% 24/121669
Progress 0.0% 25/121669
Progress 0.0% 26/121669
Progress 0.0% 27/121669
Progress 0.0% 28/121669
Progress 0.0% 29/121669
Progress 0.0% 30/121669
Progress 0.0% 31/121669
Progress 0.0% 32/121669
Progress 0.0% 33/121669
Progress 0.0% 34/121669
Progress 0.0% 35/121669
Progress 0.0% 36/121669
Progress 0.0% 37/121669
Progress 0.0% 38/121669
Progress 0.0% 39/121669
Progress 0.0% 40/121669
Progress 0.0% 41/121669
Progress 0.0% 42/121669
P

Progress 0.3% 339/121669
Progress 0.3% 340/121669
Progress 0.3% 341/121669
Progress 0.3% 342/121669
Progress 0.3% 343/121669
Progress 0.3% 344/121669
Progress 0.3% 345/121669
Progress 0.3% 346/121669
Progress 0.3% 347/121669
Progress 0.3% 348/121669
Progress 0.3% 349/121669
Progress 0.3% 350/121669
Progress 0.3% 351/121669
Progress 0.3% 352/121669
Progress 0.3% 353/121669
Progress 0.3% 354/121669
Progress 0.3% 355/121669
Progress 0.3% 356/121669
Progress 0.3% 357/121669
Progress 0.3% 358/121669
Progress 0.3% 359/121669
Progress 0.3% 360/121669
Progress 0.3% 361/121669
Progress 0.3% 362/121669
Progress 0.3% 363/121669
Progress 0.3% 364/121669
Progress 0.3% 365/121669
Progress 0.3% 366/121669
Progress 0.3% 367/121669
Progress 0.3% 368/121669
Progress 0.3% 369/121669
Progress 0.3% 370/121669
Progress 0.3% 371/121669
Progress 0.3% 372/121669
Progress 0.3% 373/121669
Progress 0.3% 374/121669
Progress 0.3% 375/121669
Progress 0.3% 376/121669
Progress 0.3% 377/121669
Progress 0.3% 378/121669


Progress 0.5% 669/121669
Progress 0.6% 670/121669
Progress 0.6% 671/121669
Progress 0.6% 672/121669
Progress 0.6% 673/121669
Progress 0.6% 674/121669
Progress 0.6% 675/121669
Progress 0.6% 676/121669
Progress 0.6% 677/121669
Progress 0.6% 678/121669
Progress 0.6% 679/121669
Progress 0.6% 680/121669
Progress 0.6% 681/121669
Progress 0.6% 682/121669
Progress 0.6% 683/121669
Progress 0.6% 684/121669
Progress 0.6% 685/121669
Progress 0.6% 686/121669
Progress 0.6% 687/121669
Progress 0.6% 688/121669
Progress 0.6% 689/121669
Progress 0.6% 690/121669
Progress 0.6% 691/121669
Progress 0.6% 692/121669
Progress 0.6% 693/121669
Progress 0.6% 694/121669
Progress 0.6% 695/121669
Progress 0.6% 696/121669
Progress 0.6% 697/121669
Progress 0.6% 698/121669
Progress 0.6% 699/121669
Progress 0.6% 700/121669
Progress 0.6% 701/121669
Progress 0.6% 702/121669
Progress 0.6% 703/121669
Progress 0.6% 704/121669
Progress 0.6% 705/121669
Progress 0.6% 706/121669
Progress 0.6% 707/121669
Progress 0.6% 708/121669


Progress 0.8% 997/121669
Progress 0.8% 998/121669
Progress 0.8% 999/121669
Progress 0.8% 1000/121669
Progress 0.8% 1001/121669
Progress 0.8% 1002/121669
Progress 0.8% 1003/121669
Progress 0.8% 1004/121669
Progress 0.8% 1005/121669
Progress 0.8% 1006/121669
Progress 0.8% 1007/121669
Progress 0.8% 1008/121669
Progress 0.8% 1009/121669
Progress 0.8% 1010/121669
Progress 0.8% 1011/121669
Progress 0.8% 1012/121669
Progress 0.8% 1013/121669
Progress 0.8% 1014/121669
Progress 0.8% 1015/121669
Progress 0.8% 1016/121669
Progress 0.8% 1017/121669
Progress 0.8% 1018/121669
Progress 0.8% 1019/121669
Progress 0.8% 1020/121669
Progress 0.8% 1021/121669
Progress 0.8% 1022/121669
Progress 0.8% 1023/121669
Progress 0.8% 1024/121669
Progress 0.8% 1025/121669
Progress 0.8% 1026/121669
Progress 0.8% 1027/121669
Progress 0.8% 1028/121669
Progress 0.8% 1029/121669
Progress 0.8% 1030/121669
Progress 0.8% 1031/121669
Progress 0.8% 1032/121669
Progress 0.8% 1033/121669
Progress 0.8% 1034/121669
Progress 0.9% 1

Progress 1.1% 1315/121669
Progress 1.1% 1316/121669
Progress 1.1% 1317/121669
Progress 1.1% 1318/121669
Progress 1.1% 1319/121669
Progress 1.1% 1320/121669
Progress 1.1% 1321/121669
Progress 1.1% 1322/121669
Progress 1.1% 1323/121669
Progress 1.1% 1324/121669
Progress 1.1% 1325/121669
Progress 1.1% 1326/121669
Progress 1.1% 1327/121669
Progress 1.1% 1328/121669
Progress 1.1% 1329/121669
Progress 1.1% 1330/121669
Progress 1.1% 1331/121669
Progress 1.1% 1332/121669
Progress 1.1% 1333/121669
Progress 1.1% 1334/121669
Progress 1.1% 1335/121669
Progress 1.1% 1336/121669
Progress 1.1% 1337/121669
Progress 1.1% 1338/121669
Progress 1.1% 1339/121669
Progress 1.1% 1340/121669
Progress 1.1% 1341/121669
Progress 1.1% 1342/121669
Progress 1.1% 1343/121669
Progress 1.1% 1344/121669
Progress 1.1% 1345/121669
Progress 1.1% 1346/121669
Progress 1.1% 1347/121669
Progress 1.1% 1348/121669
Progress 1.1% 1349/121669
Progress 1.1% 1350/121669
Progress 1.1% 1351/121669
Progress 1.1% 1352/121669
Progress 1.1

...

Progress 99.0% 120433/121669
Progress 99.0% 120434/121669
Progress 99.0% 120435/121669
Progress 99.0% 120436/121669
Progress 99.0% 120437/121669
Progress 99.0% 120438/121669
Progress 99.0% 120439/121669
Progress 99.0% 120440/121669
Progress 99.0% 120441/121669
Progress 99.0% 120442/121669
Progress 99.0% 120443/121669
Progress 99.0% 120444/121669
Progress 99.0% 120445/121669
Progress 99.0% 120446/121669
Progress 99.0% 120447/121669
Progress 99.0% 120448/121669
Progress 99.0% 120449/121669
Progress 99.0% 120450/121669
Progress 99.0% 120451/121669
Progress 99.0% 120452/121669
Progress 99.0% 120453/121669
Progress 99.0% 120454/121669
Progress 99.0% 120455/121669
Progress 99.0% 120456/121669
Progress 99.0% 120457/121669
Progress 99.0% 120458/121669
Progress 99.0% 120459/121669
Progress 99.0% 120460/121669
Progress 99.0% 120461/121669
Progress 99.0% 120462/121669
Progress 99.0% 120463/121669
Progress 99.0% 120464/121669
Progress 99.0% 120465/121669
Progress 99.0% 120466/121669
Progress 99.0%

Progress 99.2% 120716/121669
Progress 99.2% 120717/121669
Progress 99.2% 120718/121669
Progress 99.2% 120719/121669
Progress 99.2% 120720/121669
Progress 99.2% 120721/121669
Progress 99.2% 120722/121669
Progress 99.2% 120723/121669
Progress 99.2% 120724/121669
Progress 99.2% 120725/121669
Progress 99.2% 120726/121669
Progress 99.2% 120727/121669
Progress 99.2% 120728/121669
Progress 99.2% 120729/121669
Progress 99.2% 120730/121669
Progress 99.2% 120731/121669
Progress 99.2% 120732/121669
Progress 99.2% 120733/121669
Progress 99.2% 120734/121669
Progress 99.2% 120735/121669
Progress 99.2% 120736/121669
Progress 99.2% 120737/121669
Progress 99.2% 120738/121669
Progress 99.2% 120739/121669
Progress 99.2% 120740/121669
Progress 99.2% 120741/121669
Progress 99.2% 120742/121669
Progress 99.2% 120743/121669
Progress 99.2% 120744/121669
Progress 99.2% 120745/121669
Progress 99.2% 120746/121669
Progress 99.2% 120747/121669
Progress 99.2% 120748/121669
Progress 99.2% 120749/121669
Progress 99.2%

Progress 99.5% 121000/121669
Progress 99.5% 121001/121669
Progress 99.5% 121002/121669
Progress 99.5% 121003/121669
Progress 99.5% 121004/121669
Progress 99.5% 121005/121669
Progress 99.5% 121006/121669
Progress 99.5% 121007/121669
Progress 99.5% 121008/121669
Progress 99.5% 121009/121669
Progress 99.5% 121010/121669
Progress 99.5% 121011/121669
Progress 99.5% 121012/121669
Progress 99.5% 121013/121669
Progress 99.5% 121014/121669
Progress 99.5% 121015/121669
Progress 99.5% 121016/121669
Progress 99.5% 121017/121669
Progress 99.5% 121018/121669
Progress 99.5% 121019/121669
Progress 99.5% 121020/121669
Progress 99.5% 121021/121669
Progress 99.5% 121022/121669
Progress 99.5% 121023/121669
Progress 99.5% 121024/121669
Progress 99.5% 121025/121669
Progress 99.5% 121026/121669
Progress 99.5% 121027/121669
Progress 99.5% 121028/121669
Progress 99.5% 121029/121669
Progress 99.5% 121030/121669
Progress 99.5% 121031/121669
Progress 99.5% 121032/121669
Progress 99.5% 121033/121669
Progress 99.5%

Progress 99.7% 121286/121669
Progress 99.7% 121287/121669
Progress 99.7% 121288/121669
Progress 99.7% 121289/121669
Progress 99.7% 121290/121669
Progress 99.7% 121291/121669
Progress 99.7% 121292/121669
Progress 99.7% 121293/121669
Progress 99.7% 121294/121669
Progress 99.7% 121295/121669
Progress 99.7% 121296/121669
Progress 99.7% 121297/121669
Progress 99.7% 121298/121669
Progress 99.7% 121299/121669
Progress 99.7% 121300/121669
Progress 99.7% 121301/121669
Progress 99.7% 121302/121669
Progress 99.7% 121303/121669
Progress 99.7% 121304/121669
Progress 99.7% 121305/121669
Progress 99.7% 121306/121669
Progress 99.7% 121307/121669
Progress 99.7% 121308/121669
Progress 99.7% 121309/121669
Progress 99.7% 121310/121669
Progress 99.7% 121311/121669
Progress 99.7% 121312/121669
Progress 99.7% 121313/121669
Progress 99.7% 121314/121669
Progress 99.7% 121315/121669
Progress 99.7% 121316/121669
Progress 99.7% 121317/121669
Progress 99.7% 121318/121669
Progress 99.7% 121319/121669
Progress 99.7%

Progress 99.9% 121569/121669
Progress 99.9% 121570/121669
Progress 99.9% 121571/121669
Progress 99.9% 121572/121669
Progress 99.9% 121573/121669
Progress 99.9% 121574/121669
Progress 99.9% 121575/121669
Progress 99.9% 121576/121669
Progress 99.9% 121577/121669
Progress 99.9% 121578/121669
Progress 99.9% 121579/121669
Progress 99.9% 121580/121669
Progress 99.9% 121581/121669
Progress 99.9% 121582/121669
Progress 99.9% 121583/121669
Progress 99.9% 121584/121669
Progress 99.9% 121585/121669
Progress 99.9% 121586/121669
Progress 99.9% 121587/121669
Progress 99.9% 121588/121669
Progress 99.9% 121589/121669
Progress 99.9% 121590/121669
Progress 99.9% 121591/121669
Progress 99.9% 121592/121669
Progress 99.9% 121593/121669
Progress 99.9% 121594/121669
Progress 99.9% 121595/121669
Progress 99.9% 121596/121669
Progress 99.9% 121597/121669
Progress 99.9% 121598/121669
Progress 99.9% 121599/121669
Progress 99.9% 121600/121669
Progress 99.9% 121601/121669
Progress 99.9% 121602/121669
Progress 99.9%

#### Creating a Dataframe of Results sorted by F1Score

In [64]:
# Converting to Dataframe and Sorting
scoresDF = pd.DataFrame(scores)
scoresDF.columns = ["trainScore", "testScore", "precisionScore","accuracyScore", "f1Score","recallScore", "classificationReport", "Features"]
scoresDF = scoresDF.sort_values(["f1Score"], ascending=False)
scoresDF

trainScore  testScore  precisionScore  accuracyScore   f1Score  \
37367     0.865699   0.809783        0.492683       0.836735  0.457014   
63466     0.864791   0.809783        0.515957       0.842857  0.456471   
15807     0.864791   0.812500        0.468750       0.829252  0.455531   
15687     0.865699   0.809783        0.500000       0.838776  0.452656   
1574      0.864791   0.812500        0.469767       0.829932  0.446903   
...            ...        ...             ...            ...       ...   
52809     0.848457   0.820652        0.000000       0.838776  0.000000   
52805     0.849365   0.823370        0.000000       0.838776  0.000000   
52795     0.855717   0.823370        0.000000       0.838776  0.000000   
52789     0.850272   0.826087        0.000000       0.838776  0.000000   
121668    0.862976   0.842391        0.000000       0.838776  0.000000   

        recallScore                               classificationReport  \
37367      0.426160                precision    recall  f1-score   ...   
63466      0.409283                precision    recall  f1-score   ...   
15807      0.443038                precision    recall  f1-score   ...   
15687      0.413502                precision    recall  f1-score   ...   
1574       0.426160                precision    recall  f1-score   ...   
...             ...                                                ...   
52809      0.000000                precision    recall  f1-score   ...   
52805      0.000000                precision    recall  f1-score   ...   
52795      0.000000                precision    recall  f1-score   ...   
52789      0.000000                precision    recall  f1-score   ...   
121668     0.000000                precision    recall  f1-score   ...   

                                                 Features  
37367   (OverTime, Fidelity, Stability, StockOptionLev...  
63466   (OverTime, Fidelity, Stability, StockOptionLev...  
15807   (OverTime, Fidelity, Stability, Hrate_Mrate, S...  
15687   (OverTime, Fidelity, Stability, StockOptionLev...  
1574    (OverTime, Fidelity, Stability, SalesDpt, Mari...  
...                                                   ...  
52809   (Fidelity, Hrate_Mrate, HourlyRate, SalesDpt, ...  
52805   (Fidelity, Hrate_Mrate, HourlyRate, SalesDpt, ...  
52795   (Fidelity, StockOptionLevel, MaritalStatus, Ge...  
52789   (Fidelity, StockOptionLevel, PerformanceRating...  
121668  (Time_in_each_comp, Fidelity, Stability, Years...  

[121669 rows x 8 columns]

#### Feature Importance on Top Models

In [13]:
scoresDF.to_csv('scoresDF6.csv', index=False, header=True)
filterDF = pd.read_csv("scoresDF6.csv")
filterDF = filterDF.loc[filterDF["f1Score"]>.35].loc[filterDF["precisionScore"]>.35].loc[filterDF["accuracyScore"]>.7].loc[filterDF["recallScore"]>.35]
countDict = {} 
for feature in features:
    countDict[feature] = len(filterDF[filterDF['Features'].str.contains(feature)])

sortedDict = sorted(countDict.items(), key=lambda x: x[1], reverse=True)
for i in sortedDict:
    print(i[0], i[1])

Fidelity 193
OverTime 182
MaritalStatus 144
HourlyRate 138
SalesDpt 125
Gender 120
YearsWithCurrManager 116
Stability 111
StockOptionLevel 106
Hrate_Mrate 103
Education 94
PerformanceRating 74
TrainingTimesLastYear 57
Time_in_each_comp 51
TotalSatisfaction_mean 13
Income_YearsComp 0
Income_Distance 0


#### Classification Reports on Best Models

In [81]:
print(scoresDF.loc[15807][7])
print(scoresDF.loc[15807][6])
print(scoresDF.loc[15687][7])
print(scoresDF.loc[15687][6])
print(scoresDF.loc[1574][7])
print(scoresDF.loc[1574][6])
print(scoresDF.loc[1959][7])
print(scoresDF.loc[1959][6])
print(scoresDF.loc[15687][7])
print(scoresDF.loc[15687][6])
print(scoresDF.loc[2079][7])
print(scoresDF.loc[2079][6])

('OverTime', 'Fidelity', 'Stability', 'StockOptionLevel', 'Hrate_Mrate', 'SalesDpt', 'MaritalStatus', 'Gender', 'Education')
              precision    recall  f1-score   support

           0       0.89      0.93      0.91      1233
           1       0.52      0.41      0.46       237

    accuracy                           0.84      1470
   macro avg       0.70      0.67      0.68      1470
weighted avg       0.83      0.84      0.84      1470

('OverTime', 'Fidelity', 'Stability', 'StockOptionLevel', 'SalesDpt', 'MaritalStatus', 'Gender')
              precision    recall  f1-score   support

           0       0.89      0.92      0.91      1233
           1       0.50      0.41      0.45       237

    accuracy                           0.84      1470
   macro avg       0.70      0.67      0.68      1470
weighted avg       0.83      0.84      0.83      1470

('OverTime', 'Fidelity', 'Stability', 'SalesDpt', 'MaritalStatus', 'Gender')
              precision    recall  f1-score   s